In [1]:
# Imports
import openai
import langchain
import pinecone
from langchain.document_loaders import PyPDFDirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.embeddings.openai import OpenAIEmbeddings
from langchain.vectorstores import Pinecone
from langchain.llms import OpenAI

In [2]:
from dotenv import load_dotenv
load_dotenv()

True

In [3]:
import os

In [4]:
# Lets read the document
def read_doc(directory):
    file_loader = PyPDFDirectoryLoader(directory)
    documents = file_loader.load()
    return documents

In [5]:
doc = read_doc("documents/")

In [6]:
# Divide the docs into chunks
def chunk_data(docs, chunk_size=800,chunk_overlap=50):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=chunk_size,chunk_overlap=chunk_overlap)
    doc = text_splitter.split_documents(docs)
    return docs

In [7]:
documents = chunk_data(docs=doc)
documents

[Document(page_content='GOVERNMENT OF INDIA\nBUDGET 2023-2024\nSPEECH\nOF\nNIRMALA SITHARAMAN\nMINISTER OF FINANCE\nFebruary 1,  2023', metadata={'source': 'documents/budget_speech.pdf', 'page': 0}),
 Document(page_content='', metadata={'source': 'documents/budget_speech.pdf', 'page': 1}),
 Document(page_content='CONTENTS \nPART-A \n Page No.  \n\uf0b7 Introduction 1 \n\uf0b7 Achievements since 2014: Leaving no one behind 2 \n\uf0b7 Vision for Amrit Kaal  – an empowered and inclusive economy 3 \n\uf0b7 Priorities of this Budget 5 \ni. Inclusive Development  \nii. Reaching the Last Mile \niii. Infrastructure and Investment \niv. Unleashing the Potential \nv. Green Growth \nvi. Youth Power  \nvii. Financial Sector  \n \n \n \n \n \n \n \n \n\uf0b7 Fiscal Management 24 \nPART B  \n  \nIndirect Taxes  27 \n\uf0b7 Green Mobility  \n\uf0b7 Electronics   \n\uf0b7 Electrical   \n\uf0b7 Chemicals and Petrochemicals   \n\uf0b7 Marine products  \n\uf0b7 Lab Grown Diamonds  \n\uf0b7 Precious Metal

## Inserting vectors into the DB from the source

In [8]:
# Initialize embedding technique of OpenAI
embeddings = OpenAIEmbeddings(api_key="")
embeddings

/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `OpenAIEmbeddings` was deprecated in LangChain 0.0.9 and will be removed in 0.3.0. An updated version of the class exists in the langchain-openai package and should be used instead. To use it run `pip install -U langchain-openai` and import as `from langchain_openai import OpenAIEmbeddings`.
  warn_deprecated(


OpenAIEmbeddings(client=<openai.resources.embeddings.Embeddings object at 0x1206fc790>, async_client=<openai.resources.embeddings.AsyncEmbeddings object at 0x1206fe980>, model='text-embedding-ada-002', deployment='text-embedding-ada-002', openai_api_version='', openai_api_base=None, openai_api_type='', openai_proxy='', embedding_ctx_length=8191, openai_api_key='sk-proj-lqzT7oZpWEq3SSqM64kpT3BlbkFJznFvEi5y5OpPNifszWmv', openai_organization=None, allowed_special=set(), disallowed_special='all', chunk_size=1000, max_retries=2, request_timeout=None, headers=None, tiktoken_enabled=True, tiktoken_model_name=None, show_progress_bar=False, model_kwargs={}, skip_empty=False, default_headers=None, default_query=None, retry_min_seconds=4, retry_max_seconds=20, http_client=None)

In [9]:
vectors = embeddings.embed_query("How are you?")
vectors

[-0.016785908412158042,
 -0.012151270116836888,
 0.006627965687606043,
 -0.026018159342696565,
 -0.01616878054948239,
 0.01762520513661754,
 -0.011114493891931487,
 -0.0099234347700346,
 -0.018131250431046412,
 -0.010417137246439636,
 0.0278695466560138,
 0.0016508201293049156,
 -0.00733766375413787,
 -0.011651395765758651,
 0.007238923072592348,
 -0.015391197915142053,
 0.028363250063741408,
 -0.011830363367475229,
 0.013959458032731997,
 -0.0205997656070393,
 0.00252868606461311,
 0.006344086460993312,
 0.0009997490514024384,
 -0.008263357876457773,
 -0.01588490039154709,
 -0.007794339173455263,
 0.025117151322085612,
 -0.012404292764051323,
 0.02230304282936083,
 -0.02515417884483454,
 0.005609702758413819,
 0.0076955989575710265,
 -0.013169533511690397,
 0.004014424029647617,
 0.008757060352862809,
 -0.022290699080014423,
 0.004020595438659533,
 -0.01043565193913667,
 0.0203282291984504,
 -0.006337915051981395,
 0.0270302499315543,
 0.001255857519538152,
 -0.005239425202618115,
 -0

In [10]:
len(vectors) # dimension of vector database

1536

In [11]:
def generate_embeddings(documents):
    texts = [doc.page_content for doc in documents] 
    vectors = embeddings.embed_documents(texts)
    return vectors

vectors = generate_embeddings(documents)
vectors

[[-0.004032620756198555,
  -0.032052491350715674,
  -0.025433522106990125,
  0.029055715051871694,
  0.012521319282930906,
  -0.008690655364466929,
  -0.022084949876072592,
  -0.005537523972790965,
  -0.00954408585729172,
  -0.009035936695031357,
  0.038150285023130365,
  0.010599472722189791,
  -0.007941461289755935,
  -0.0014992032895178955,
  -0.021381358011925485,
  -0.009185775323709037,
  0.01743342940365205,
  0.00032288651476187693,
  0.0242348112149235,
  -0.010514781039925966,
  0.005693877668639068,
  -0.0002485778278991934,
  0.016612572849695483,
  0.009524542052764338,
  0.0020325971147027414,
  -0.014423622039144641,
  0.020664736944760124,
  -0.025550788659444764,
  -0.00727044336447705,
  0.018241256754590363,
  -0.016469247891204342,
  -0.016742866742523198,
  0.016912250107050848,
  -0.020834120309287774,
  -0.005263905121472109,
  -0.03716004324200097,
  -0.007381193918438676,
  0.0006022057588165419,
  0.009941484931251748,
  -0.014110914647448436,
  0.016664689661

In [12]:
from pinecone import Pinecone

In [31]:
# Vector search db in pinecone
pc = Pinecone(api_key="") 
index = pc.Index("langchain-index")

In [32]:
def createVectors(vectors,documents):
    upsert_vectors = [
        {"id": f"vec{i}", "values": vector, "metadata": {"text": doc.page_content, "genre": "action"}}
        for i, (vector, doc) in enumerate(zip(vectors, documents))
    ]
    index.upsert(vectors=upsert_vectors, namespace="ns1")
    return upsert_vectors

In [22]:
upsert_vectors = createVectors(vectors,documents)
upsert_vectors

[{'id': 'vec0',
  'values': [-0.004032620756198555,
   -0.032052491350715674,
   -0.025433522106990125,
   0.029055715051871694,
   0.012521319282930906,
   -0.008690655364466929,
   -0.022084949876072592,
   -0.005537523972790965,
   -0.00954408585729172,
   -0.009035936695031357,
   0.038150285023130365,
   0.010599472722189791,
   -0.007941461289755935,
   -0.0014992032895178955,
   -0.021381358011925485,
   -0.009185775323709037,
   0.01743342940365205,
   0.00032288651476187693,
   0.0242348112149235,
   -0.010514781039925966,
   0.005693877668639068,
   -0.0002485778278991934,
   0.016612572849695483,
   0.009524542052764338,
   0.0020325971147027414,
   -0.014423622039144641,
   0.020664736944760124,
   -0.025550788659444764,
   -0.00727044336447705,
   0.018241256754590363,
   -0.016469247891204342,
   -0.016742866742523198,
   0.016912250107050848,
   -0.020834120309287774,
   -0.005263905121472109,
   -0.03716004324200097,
   -0.007381193918438676,
   0.0006022057588165419,
 

## Using the question and finding the closest matches

In [24]:
QUERY = "What is India's budget?"

In [17]:
def get_query(QUERY):
    query_vector = embeddings.embed_query(QUERY)
    query_results = index.query(
        namespace="ns1",
        vector=query_vector,
        top_k=2,
        include_values=True,
        include_metadata=True,
        filter={"genre": {"$eq": "action"}}
    )
    return query_results

In [18]:
query_results = get_query(QUERY)
query_results

{'matches': [{'id': 'vec4',
              'metadata': {'genre': 'action',
                           'text': 'Budget 2023-2024 \n'
                                   ' \n'
                                   'Speech of  \n'
                                   'Nirmala Sitharaman \n'
                                   'Minister of Finance \n'
                                   'February 1, 2023 \n'
                                   'Hon’ble Speaker,  \n'
                                   ' I present the Budget for 2023-24. This is '
                                   'the first Budget in Amrit \n'
                                   'Kaal . \n'
                                   'Introduction \n'
                                   '1. This Budget hopes to build on the '
                                   'foundation laid in the previous \n'
                                   'Budget, and the blueprint drawn for '
                                   'India@100. We envision a prosperous \n'

In [29]:
def convert_to_text(query_results):
    relevant_text = "These information may be useful: "
    for match in query_results['matches']:
        relevant_text += match['metadata']['text']
    return relevant_text

In [30]:
convert_to_text(get_query(QUERY="How much will the agriculture target be increased in crores?"))

"These information may be useful: 7 \n \n \n farmers in contributing to the health of fellow citizens by growing these \n‘Shree Anna’.   \n22. Now to make India a global hub for ' Shree Anna' , the Indian Institute \nof Millet Research, Hyderabad  will be supported as the Centre of Excellence \nfor sharing best practices, research and technologies at the international \nlevel.    \nAgriculture Credit  \n23. The agriculture credit target will be increased  \nto ` 20 lakh crore with focus on animal husbandry, dairy and fisheries.  \nFisheries \n24. We will launch a new sub-scheme of PM Matsya Sampada Yojana \nwith targeted investment of ` 6,000 crore to further enable activities of \nfishermen, fish vendors, and micro & small enterprises, improve value chain \nefficiencies, and expand the market. \nCooperation \n25. For farmers, especially small and marginal farmers, and other \nmarginalised sections, the government is promoting cooperative-based \neconomic development model. A new Minis